In [2]:
import numpy as np
import open3d as o3d
import os

Rename the files in the format '00..0n'

In [11]:
label_folder = '/mnt/ssd/Datasets/cielo_falcon/label/'
point_folder = '/mnt/ssd/Datasets/cielo_falcon/lidar_bin/'

c = 0
for i,label_filename in enumerate(os.listdir(label_folder)):
    point_filename = label_filename[:-5] + '.bin'
    new_name = '{:06d}'.format(i)
    # Construct full paths for the old and new names
    old_point_path = os.path.join(point_folder, point_filename)
    new_point_path = os.path.join(point_folder, new_name + '.bin')
    
    old_label_path = os.path.join(label_folder, label_filename)
    new_label_path = os.path.join(label_folder, new_name + '.json')
    

    if not os.path.exists(new_point_path) and not os.path.exists(new_label_path):
        # Rename files
        os.rename(old_point_path, new_point_path)
        os.rename(old_label_path, new_label_path)
        c += 1
    else:
        print("Error with duplicate names!")
print("Renamed {} files".format(str(c)))
    

Renamed 235 files


Convert json files to txt KITTI format

In [12]:
import json

def convert_json_to_txt(json_file, txt_file):
    with open(json_file, 'r') as f:
        data = json.load(f)

    with open(txt_file, 'w') as f:
        for item in data:
            obj_id = item['obj_id']
            category_name = item['obj_type']
            position = item['psr']['position']
            rotation = item['psr']['rotation']
            scale = item['psr']['scale']

            x, y, z = position['x'], position['y'], position['z']
            dx, dy, dz = scale['x'], scale['y'], scale['z']
            yaw = rotation['z']

            line = f"{category_name} {x:.3f} {y:.3f} {z:.3f} {dx:.3f} {dy:.3f} {dz:.3f} {yaw:.3f}\n"
            f.write(line)

label_folder = '/mnt/ssd/Datasets/cielo_falcon/label/'
label_dest_folder = '/mnt/ssd/Datasets/cielo_falcon/labels/'
if not os.path.exists(label_dest_folder):
    os.makedirs(label_dest_folder)

for filename in os.listdir(label_folder):
    # Replace 'input.json' and 'output.txt' with your actual input and output file paths
    convert_json_to_txt(os.path.join(label_folder,filename), os.path.join(label_dest_folder,filename[:-5]+'.txt'))


Convert .pcd files to .bin according to KITTI format

In [13]:
pcd_folder = '/mnt/ssd/Datasets/cielo_falcon/lidar/'
pcd_dest_folder = '/mnt/ssd/Datasets/cielo_falcon/points'
if not os.path.exists(pcd_dest_folder):
    os.makedirs(pcd_dest_folder)

for pcd_filename in os.listdir(pcd_folder):
    pcd_path = os.path.join(pcd_folder,pcd_filename)
    pcd_data =  o3d.io.read_point_cloud(pcd_path)
    points = np.asarray(pcd_data.points)
    print(points[0])
    # add fake intensity
    points = np.hstack([points, np.zeros((points.shape[0],1))],dtype=np.float32)
    with open(os.path.join(pcd_dest_folder,pcd_filename[:-4]+".bin"), 'wb') as f:
        f.write(points.tobytes())

Create Training Testing Structure

In [3]:
training_folder = "/mnt/ssd/Datasets/cielo_falcon/training"
training_lidars_folder = os.path.join(training_folder,"velodyne")
training_labels_folder = os.path.join(training_folder,"label_2")

testing_folder = "/mnt/ssd/Datasets/cielo_falcon/testing"
testing_lidars_folder = os.path.join(testing_folder,"velodyne")

os.makedirs(training_lidars_folder)
os.makedirs(training_labels_folder)

os.makedirs(testing_lidars_folder)


FileExistsError: [Errno 17] File exists: '/mnt/ssd/Datasets/cielo_falcon/training/velodyne'

Split Dataset

In [4]:
train = 0.9
val  = 0.1
test = 0.0

label_folder = '/mnt/ssd/Datasets/cielo_falcon/labels/'
train_folder = "/mnt/ssd/Datasets/cielo_falcon/lidar_bin"
train_samples_files = os.listdir(train_folder)

trainval_file = "trainval.txt"
train_file = "train.txt"
val_file = "val.txt"
test_file = "test.txt"
n_test = int(test * len(train_samples_files))
n_trainval = len(train_samples_files) - n_test
n_train =  int(train*n_trainval)
n_val  = n_trainval - n_train

from sklearn.model_selection import train_test_split
import shutil
# Specify the proportion for the validation set (e.g., 20% for validation)
validation_size = 0.1
# Split the list into training and validation sets

train_set, validation_set = train_test_split(train_samples_files, test_size=validation_size, random_state=42)

image_set_dir = "/mnt/ssd/Datasets/cielo_falcon/ImageSets"
if not os.path.exists(image_set_dir):
    os.makedirs(image_set_dir)
with open(os.path.join(image_set_dir,trainval_file), "w") as f:
    for filename in train_set + validation_set:
        f.write(filename[:-4]+"\n")
        shutil.copy(os.path.join(train_folder,filename), training_lidars_folder)
        shutil.copy(os.path.join(label_folder,filename[:-4]+".txt"), training_labels_folder)
with open(os.path.join(image_set_dir,train_file), "w") as f:
    for filename in train_set:
        f.write(filename[:-4]+"\n")
with open(os.path.join(image_set_dir,val_file), "w") as f:
    for filename in validation_set:
        f.write(filename[:-4]+"\n")



In [6]:
import pickle

# Replace 'your_file.pkl' with the path to your PKL file
file_path = '../data/kitti/kitti_dbinfos_train.pkl'

# Reading the PKL file
with open(file_path, 'rb') as file:
    data = pickle.load(file)

# Now, 'data' contains the contents of the PKL file
print(data)

{'Pedestrian': [{'name': 'Pedestrian', 'path': 'kitti_gt_database/0_Pedestrian_0.bin', 'image_idx': 0, 'gt_idx': 0, 'box3d_lidar': array([ 8.73138  , -1.8559175, -1.5996994,  1.2      ,  0.48     ,
        1.89     , -1.5807964], dtype=float32), 'num_points_in_gt': 377, 'difficulty': 0, 'group_id': 0, 'score': 0.0}, {'name': 'Pedestrian', 'path': 'kitti_gt_database/4_Pedestrian_2.bin', 'image_idx': 4, 'gt_idx': 2, 'box3d_lidar': array([23.799772 , -8.312204 , -1.4643983,  1.09     ,  0.72     ,
        1.96     ,  2.962389 ], dtype=float32), 'num_points_in_gt': 23, 'difficulty': 2, 'group_id': 11, 'score': 0.0}, {'name': 'Pedestrian', 'path': 'kitti_gt_database/5_Pedestrian_0.bin', 'image_idx': 5, 'gt_idx': 0, 'box3d_lidar': array([12.708357 , -5.045034 , -1.4257739,  1.04     ,  0.42     ,
        1.9      , -2.2507963], dtype=float32), 'num_points_in_gt': 152, 'difficulty': 1, 'group_id': 18, 'score': 0.0}, {'name': 'Pedestrian', 'path': 'kitti_gt_database/5_Pedestrian_1.bin', 'image